# Importing required libraries

In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from scipy.spatial.distance import squareform
from scipy.cluster.hierarchy import linkage, dendrogram, fcluster
import seaborn as sns
from collections import Counter

# Importing shifted wobble dataset

In [3]:
all_RMSD = pd.read_excel('shifted_wobbles.xlsx', sheet_name='all_against_all_nr_sw')

In [4]:
sw_names= [j.rstrip('.cif') for i,j in enumerate(list(all_RMSD.columns)[1:])]

all_RMSD1= all_RMSD.drop(['#'], axis=1)
all_RMSD1.shape

all_RMSD1.index= sw_names
all_RMSD1.columns= sw_names

In [5]:
# Convert DataFrame to squareform distance matrix
rmsd_matrix = squareform(all_RMSD1.values)

# Perform hierarchical clustering
linkage_matrix = linkage(rmsd_matrix, method='average')

dend = dendrogram(linkage_matrix, color_threshold= 1.23, labels=all_RMSD1.index, above_threshold_color='lightgray', leaf_rotation=0, orientation='left', no_plot=True)

color_list_counter=  dict(Counter(dend['color_list']))
lcolor_list_counter=  dict(Counter(dend['leaves_color_list']))

small_clusters=[] #clusters with less than 4 members will be stored here

for i in lcolor_list_counter:
    if i != 'lightgray' and lcolor_list_counter[i]<4:
        small_clusters.append(i)

color_list_n= [] #updated color list for the branches
leaves_color_list_n= [] #updated color list for the branch leaves

for i, cls in enumerate(dend['color_list']):
    if cls in small_clusters:
        color_list_n.append('lightgray')
    else:
        if cls =='C1':
            color_list_n.append('b')
        elif cls =='C3':
            color_list_n.append('r')
        elif cls =='C5':
            color_list_n.append('g')
        elif cls =='C6':
            color_list_n.append('magenta')
        elif cls =='lightgray':
            color_list_n.append('lightgray')

for i, ls in enumerate(dend['leaves_color_list']):
    if ls in small_clusters:
      leaves_color_list_n.append('lightgray')
    else:
        if ls =='C1':
            leaves_color_list_n.append('b')
        elif ls =='C3':
            leaves_color_list_n.append('r')
        elif ls =='C5':
            leaves_color_list_n.append('g')
        elif ls =='C6':
            leaves_color_list_n.append('magenta')
        elif ls =='lightgray':
            leaves_color_list_n.append('lightgray')

dend["color_list"]= color_list_n #updated branch color list is assigned to the original dendrogram
dend["leaves_color_list"]= leaves_color_list_n #updated leaves color list is assigned to the original dendrogram

#Re-ploting the dendrogram with the updated colors
plt.figure(figsize=(12, 11), dpi = 2000)

dendrogram(linkage_matrix, color_threshold= 1.23, above_threshold_color='lightgray', leaf_rotation=0, leaf_font_size=12, orientation='left', labels=all_RMSD1.index)

#assigning branch color
for i, dcoord in enumerate(dend['dcoord']):
    plt.plot(dcoord, dend['icoord'][i], color=dend['color_list'][i])

#assigning branch leaves color
for leaf, leaf_color in zip(plt.gca().get_yticklabels(), dend["leaves_color_list"]):
    leaf.set_color(leaf_color)

#assigning locations for xticks
ticks_loc=[0.0, 0.5, 1.0, 1.23, 1.5, 2.0, 2.5, 3.0, 3.5, 4.0]
plt.xticks(ticks_loc, fontsize = 12)

ticks_labels = ['0.00', '0.50', '1.00', '1.23', '1.50', '2.00', '2.50', '3.00', '3.50', '4.00']
plt.gca().set_xticklabels(ticks_labels)

#updating xtick and ytick parameters
plt.tick_params(axis='y', which='both', length= -2)
plt.tick_params(axis='x', width=2, length= 5)

#ticks = plt.gca().get_xticklabels()
#xticks = plt.gca().get_xticks()
#xticklabels = plt.gca().get_xticklabels()
#for tick in ticks:
#    if tick.get_text() == '1.23':  #highlighting the color treshold
#        tick.set_color('darkorange')


tick_index = ticks_loc.index(1.23)  # Find the index of the tick at location 4
label = plt.gca().get_xticklabels()[tick_index]  # Get the tick label
label.set_color('orangered')

#assigning x-axis label
plt.xlabel('RMSD (Å)', fontsize=14)

#adding a vertical line to show the cluster cut-off
plt.axvline(x=1.23, color='orangered', linestyle='--', alpha= 0.8,  linewidth=2)

#hiding top, right, and left axis
ax= plt.gca()
ax.set_ylim(-10, 410)
ax.spines.top.set_visible(False)
ax.spines.right.set_visible(False)
ax.spines.left.set_visible(False)
ax.spines.bottom.set_linewidth(2)

plt.show()
#print (dend)